In [3]:
# Import libraries
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly
import warnings
warnings.filterwarnings('ignore')

# Set Plotly default template
import plotly.io as pio
pio.templates.default = "plotly_white"

print("✅ Libraries imported successfully!")
print(f"📦 Plotly version: {plotly.__version__}")
print(f"📦 Pandas version: {pd.__version__}")


✅ Libraries imported successfully!
📦 Plotly version: 5.24.1
📦 Pandas version: 2.1.3


## 📂 Load Sample Data

We'll use a sample e-commerce dataset for demonstrations:

In [6]:
# Load UCI Online Retail data (same as Module 3)
try:
    url = 'https://archive.ics.uci.edu/ml/machine-learning-databases/00502/online_retail_II.xlsx'
    df_raw = pd.read_excel(url, sheet_name='Year 2009-2010')
    print("✅ Data loaded from UCI repository")
    
    # Standardize column names (UCI dataset uses different names)
    column_mapping = {
        'Customer ID': 'CustomerID',
        'Invoice': 'InvoiceNo',
        'Price': 'UnitPrice'
    }
    df_raw = df_raw.rename(columns=column_mapping)
    
    # Also check and print columns to debug
    print(f"Columns: {list(df_raw.columns)}")
    
except Exception as e:
    print(f"⚠️ Could not load from UCI: {e}")
    print("Creating fallback sample data...")
    # Fallback: Create sample data
    np.random.seed(42)
    dates = pd.date_range('2023-01-01', '2023-12-31', freq='D')
    df_raw = pd.DataFrame({
        'InvoiceNo': np.random.randint(100000, 999999, 5000),
        'StockCode': np.random.choice(['A001', 'A002', 'B001', 'B002', 'C001'], 5000),
        'Description': np.random.choice(['Product A', 'Product B', 'Product C'], 5000),
        'Quantity': np.random.randint(1, 20, 5000),
        'InvoiceDate': np.random.choice(dates, 5000),
        'UnitPrice': np.random.uniform(5, 100, 5000),
        'CustomerID': np.random.randint(10000, 20000, 5000),
        'Country': 'United Kingdom'
    })

# Quick cleaning
df = df_raw.dropna(subset=['CustomerID']).copy()
df = df[(df['Quantity'] > 0) & (df['UnitPrice'] > 0)]
df['Revenue'] = df['Quantity'] * df['UnitPrice']
df['InvoiceDate'] = pd.to_datetime(df['InvoiceDate'])
df['Month'] = df['InvoiceDate'].dt.to_period('M').astype(str)
df = df[df['Country'] == 'United Kingdom']

print(f"\n📊 Dataset: {len(df):,} transactions")
print(f"📅 Date Range: {df['InvoiceDate'].min()} to {df['InvoiceDate'].max()}")
print(f"👥 Customers: {df['CustomerID'].nunique():,}")
print(f"💰 Total Revenue: £{df['Revenue'].sum():,.2f}")


✅ Data loaded from UCI repository
Columns: ['InvoiceNo', 'StockCode', 'Description', 'Quantity', 'InvoiceDate', 'UnitPrice', 'CustomerID', 'Country']

📊 Dataset: 370,929 transactions
📅 Date Range: 2009-12-01 07:45:00 to 2010-12-09 20:01:00
👥 Customers: 3,969
💰 Total Revenue: £7,414,755.96

📊 Dataset: 370,929 transactions
📅 Date Range: 2009-12-01 07:45:00 to 2010-12-09 20:01:00
👥 Customers: 3,969
💰 Total Revenue: £7,414,755.96


---

# Part 1: Plotly Interactive Charts

## 1.1 Basic Plotly Express Charts

**Plotly Express** = High-level API for quick charts

Key features:
- 🎨 Auto-styling and colors
- 📊 Built-in hover tooltips
- 🔍 Zoom, pan, reset
- 💾 Download as PNG/SVG

In [7]:
# Example 1: Interactive Line Chart
# Monthly Revenue Trend

monthly_revenue = df.groupby('Month')['Revenue'].sum().reset_index()
monthly_revenue['Revenue_K'] = monthly_revenue['Revenue'] / 1000

fig = px.line(monthly_revenue, 
              x='Month', 
              y='Revenue_K',
              title='📈 Monthly Revenue Trend (Interactive)',
              labels={'Revenue_K': 'Revenue (£ thousands)', 'Month': 'Month'},
              markers=True)

# Customize layout
fig.update_traces(line_color='#2563eb', line_width=3, marker_size=10)
fig.update_layout(
    title_font_size=18,
    title_font_color='#1e293b',
    hovermode='x unified',
    height=500
)

fig.show()

print("\n💡 Try this:")
print("  • Hover over points to see exact values")
print("  • Click and drag to zoom into a time period")
print("  • Double-click to reset zoom")
print("  • Click 📷 icon to download as PNG")


💡 Try this:
  • Hover over points to see exact values
  • Click and drag to zoom into a time period
  • Double-click to reset zoom
  • Click 📷 icon to download as PNG


In [8]:
# Example 2: Interactive Bar Chart with Sorting
# Top Products by Revenue

product_revenue = df.groupby('Description')['Revenue'].sum().reset_index()
product_revenue = product_revenue.nlargest(10, 'Revenue')
product_revenue['Revenue_K'] = product_revenue['Revenue'] / 1000

fig = px.bar(product_revenue.sort_values('Revenue_K'), 
             x='Revenue_K', 
             y='Description',
             orientation='h',
             title='💰 Top 10 Products by Revenue',
             labels={'Revenue_K': 'Revenue (£ thousands)', 'Description': 'Product'},
             color='Revenue_K',
             color_continuous_scale='Blues')

fig.update_layout(
    title_font_size=18,
    height=500,
    showlegend=False
)

fig.show()

print("\n💡 Interactive Features:")
print("  • Hover to see exact revenue amounts")
print("  • Color intensity shows relative value")
print("  • Click legend items to filter (if multiple series)")


💡 Interactive Features:
  • Hover to see exact revenue amounts
  • Color intensity shows relative value
  • Click legend items to filter (if multiple series)


In [9]:
# Example 3: Interactive Scatter Plot
# Quantity vs Price with Revenue as bubble size

# Aggregate by product
product_analysis = df.groupby('Description').agg({
    'Quantity': 'sum',
    'UnitPrice': 'mean',
    'Revenue': 'sum',
    'InvoiceNo': 'nunique'
}).reset_index()

product_analysis.columns = ['Product', 'Total_Quantity', 'Avg_Price', 'Revenue', 'Orders']
product_analysis = product_analysis.nlargest(20, 'Revenue')

fig = px.scatter(product_analysis,
                x='Total_Quantity',
                y='Avg_Price',
                size='Revenue',
                color='Orders',
                hover_name='Product',
                hover_data={'Total_Quantity': ':,', 'Avg_Price': ':.2f', 'Revenue': ':.2f'},
                title='📦 Product Analysis: Quantity vs Price<br><sub>Bubble size = Revenue | Color = Orders</sub>',
                labels={'Total_Quantity': 'Total Quantity Sold',
                       'Avg_Price': 'Average Price (£)',
                       'Orders': 'Number of Orders'},
                color_continuous_scale='Viridis')

fig.update_layout(
    title_font_size=18,
    height=600
)

fig.show()

print("\n💡 Insights to Look For:")
print("  • Top-right: High price, high volume (premium best-sellers)")
print("  • Top-left: High price, low volume (luxury items)")
print("  • Bottom-right: Low price, high volume (budget best-sellers)")
print("  • Bubble size shows total revenue contribution")


💡 Insights to Look For:
  • Top-right: High price, high volume (premium best-sellers)
  • Top-left: High price, low volume (luxury items)
  • Bottom-right: Low price, high volume (budget best-sellers)
  • Bubble size shows total revenue contribution


## 1.2 Advanced Plotly: Custom Layouts

For more control, use **Plotly Graph Objects**:

In [10]:
# Example 4: Multi-Panel Dashboard with Subplots

# Prepare data
monthly_revenue = df.groupby('Month').agg({
    'Revenue': 'sum',
    'InvoiceNo': 'nunique',
    'CustomerID': 'nunique'
}).reset_index()

# Create subplots (2 rows, 2 columns)
fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=('Monthly Revenue Trend', 'Order Volume',
                   'Unique Customers', 'Revenue Distribution'),
    specs=[[{'type': 'scatter'}, {'type': 'bar'}],
           [{'type': 'scatter'}, {'type': 'histogram'}]]
)

# Plot 1: Revenue Trend (Line)
fig.add_trace(
    go.Scatter(x=monthly_revenue['Month'], 
               y=monthly_revenue['Revenue']/1000,
               mode='lines+markers',
               name='Revenue',
               line=dict(color='#2563eb', width=3),
               marker=dict(size=8)),
    row=1, col=1
)

# Plot 2: Order Volume (Bar)
fig.add_trace(
    go.Bar(x=monthly_revenue['Month'], 
           y=monthly_revenue['InvoiceNo'],
           name='Orders',
           marker_color='#10b981'),
    row=1, col=2
)

# Plot 3: Unique Customers (Line)
fig.add_trace(
    go.Scatter(x=monthly_revenue['Month'], 
               y=monthly_revenue['CustomerID'],
               mode='lines+markers',
               name='Customers',
               line=dict(color='#8b5cf6', width=3),
               marker=dict(size=8)),
    row=2, col=1
)

# Plot 4: Revenue Distribution (Histogram)
fig.add_trace(
    go.Histogram(x=df['Revenue'],
                nbinsx=50,
                name='Revenue Dist',
                marker_color='#f59e0b'),
    row=2, col=2
)

# Update layout
fig.update_xaxes(title_text="Month", row=1, col=1)
fig.update_xaxes(title_text="Month", row=1, col=2)
fig.update_xaxes(title_text="Month", row=2, col=1)
fig.update_xaxes(title_text="Revenue (£)", row=2, col=2)

fig.update_yaxes(title_text="Revenue (£K)", row=1, col=1)
fig.update_yaxes(title_text="Orders", row=1, col=2)
fig.update_yaxes(title_text="Customers", row=2, col=1)
fig.update_yaxes(title_text="Count", row=2, col=2)

fig.update_layout(
    title_text="📊 E-commerce Performance Dashboard",
    title_font_size=20,
    height=800,
    showlegend=False
)

fig.show()

print("\n✅ Created a 2x2 interactive dashboard!")
print("💡 Each subplot is independently zoomable and hoverable")


✅ Created a 2x2 interactive dashboard!
💡 Each subplot is independently zoomable and hoverable


In [11]:
# Example 5: Animated Visualization
# Show revenue growth over time with animation

# Prepare cumulative data by month
df_sorted = df.sort_values('InvoiceDate')
df_sorted['Cumulative_Revenue'] = df_sorted['Revenue'].cumsum()
df_sorted['Month'] = df_sorted['InvoiceDate'].dt.to_period('M').astype(str)

# Sample data (take every 100th row for smoother animation)
df_anim = df_sorted.iloc[::100].copy()

fig = px.line(df_anim,
             x='InvoiceDate',
             y='Cumulative_Revenue',
             title='📈 Cumulative Revenue Growth Animation',
             labels={'Cumulative_Revenue': 'Cumulative Revenue (£)',
                    'InvoiceDate': 'Date'},
             animation_frame='Month')

fig.update_traces(line_color='#2563eb', line_width=3)
fig.update_layout(
    title_font_size=18,
    height=500,
    xaxis_range=[df_anim['InvoiceDate'].min(), df_anim['InvoiceDate'].max()],
    yaxis_range=[0, df_anim['Cumulative_Revenue'].max() * 1.1]
)

fig.show()

print("\n🎬 Click the PLAY button to see revenue accumulate over time!")
print("💡 Use the slider to jump to specific months")


🎬 Click the PLAY button to see revenue accumulate over time!
💡 Use the slider to jump to specific months


---

# Part 2: Streamlit Web Applications

## 2.1 What is Streamlit?

**Streamlit** = Python framework untuk membuat web apps tanpa HTML/CSS/JavaScript

### Key Features:
- 🐍 **Pure Python** - No web development knowledge needed
- ⚡ **Fast** - Write code, see results instantly
- 🎛️ **Built-in Widgets** - Sliders, buttons, text inputs, file uploaders
- 📊 **Data-First** - Built for data apps and ML demos
- 🚀 **Easy Deploy** - One-click deployment to Streamlit Cloud

### Streamlit Architecture:

```
User Browser ←→ Streamlit Server ←→ Python Script
                                        ↓
                                  Your Data/Models
```

When user interacts with widget → Script reruns → UI updates

---

## 2.2 Basic Streamlit App Structure

Create a file `app.py` with this structure:

```python
import streamlit as st
import pandas as pd

# 1. Page Config (must be first)
st.set_page_config(page_title="My App", page_icon="📊", layout="wide")

# 2. Title and Description
st.title("📊 My Dashboard")
st.markdown("Welcome to my dashboard!")

# 3. Sidebar (optional)
st.sidebar.header("Filters")
option = st.sidebar.selectbox("Choose option", ["A", "B", "C"])

# 4. Main Content
col1, col2 = st.columns(2)
with col1:
    st.metric("Sales", "$1.2M", "+12%")
with col2:
    st.metric("Users", "34K", "+5%")

# 5. Charts
st.line_chart(df)
```

Run with: `streamlit run app.py`

---

## 2.3 Creating Your First Streamlit App

Let's create a simple e-commerce dashboard!

### 📝 Step 1: Create `streamlit_app.py`

Copy this code into a new file called `streamlit_app.py` in your project folder:

In [ ]:
# This cell generates a Streamlit app file
# Run this cell to create streamlit_app.py

streamlit_code = '''
import streamlit as st
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from datetime import datetime

# Page Config
st.set_page_config(
    page_title="E-commerce Dashboard",
    page_icon="🛒",
    layout="wide",
    initial_sidebar_state="expanded"
)

# Custom CSS
st.markdown("""
    <style>
    .main {background-color: #f8fafc;}
    .stMetric {background-color: white; padding: 15px; border-radius: 10px; box-shadow: 0 2px 4px rgba(0,0,0,0.1);}
    </style>
""", unsafe_allow_html=True)

# Title
st.title("🛒 E-commerce Performance Dashboard")
st.markdown("**Real-time insights from UK Online Retail data**")
st.markdown("---")

# Load Data
@st.cache_data
def load_data():
    """Load and cache data"""
    try:
        url = 'https://archive.ics.uci.edu/ml/machine-learning-databases/00502/online_retail_II.xlsx'
        df = pd.read_excel(url, sheet_name='Year 2009-2010')
        st.success("✅ Data loaded from UCI repository")
    except:
        st.warning("⚠️ Using sample data")
        import numpy as np
        np.random.seed(42)
        dates = pd.date_range('2023-01-01', '2023-12-31', freq='D')
        df = pd.DataFrame({
            'InvoiceNo': np.random.randint(100000, 999999, 5000),
            'Description': np.random.choice(['Product A', 'Product B', 'Product C'], 5000),
            'Quantity': np.random.randint(1, 20, 5000),
            'InvoiceDate': np.random.choice(dates, 5000),
            'UnitPrice': np.random.uniform(5, 100, 5000),
            'CustomerID': np.random.randint(10000, 20000, 5000),
            'Country': 'United Kingdom'
        })
    
    # Clean data
    df = df.dropna(subset=['CustomerID'])
    df = df[(df['Quantity'] > 0) & (df['UnitPrice'] > 0)]
    df['Revenue'] = df['Quantity'] * df['UnitPrice']
    df['InvoiceDate'] = pd.to_datetime(df['InvoiceDate'])
    df['Month'] = df['InvoiceDate'].dt.to_period('M').astype(str)
    df['Year'] = df['InvoiceDate'].dt.year
    df = df[df['Country'] == 'United Kingdom']
    
    return df

df = load_data()

# Sidebar Filters
st.sidebar.header("🔍 Filters")

# Date range filter
min_date = df['InvoiceDate'].min().date()
max_date = df['InvoiceDate'].max().date()

date_range = st.sidebar.date_input(
    "Select Date Range",
    value=(min_date, max_date),
    min_value=min_date,
    max_value=max_date
)

# Product filter
all_products = ['All'] + sorted(df['Description'].unique().tolist())
selected_product = st.sidebar.selectbox("Select Product", all_products)

# Apply filters
if len(date_range) == 2:
    df_filtered = df[(df['InvoiceDate'].dt.date >= date_range[0]) & 
                     (df['InvoiceDate'].dt.date <= date_range[1])]
else:
    df_filtered = df

if selected_product != 'All':
    df_filtered = df_filtered[df_filtered['Description'] == selected_product]

st.sidebar.markdown("---")
st.sidebar.info(f"📊 Showing **{len(df_filtered):,}** transactions")

# KPI Metrics
st.header("📊 Key Performance Indicators")

col1, col2, col3, col4 = st.columns(4)

total_revenue = df_filtered['Revenue'].sum()
total_orders = df_filtered['InvoiceNo'].nunique()
total_customers = df_filtered['CustomerID'].nunique()
avg_order_value = total_revenue / total_orders if total_orders > 0 else 0

with col1:
    st.metric("💰 Total Revenue", f"£{total_revenue/1e6:.2f}M")
with col2:
    st.metric("📦 Total Orders", f"{total_orders:,}")
with col3:
    st.metric("👥 Unique Customers", f"{total_customers:,}")
with col4:
    st.metric("💵 Avg Order Value", f"£{avg_order_value:.2f}")

st.markdown("---")

# Charts
col_left, col_right = st.columns(2)

with col_left:
    st.subheader("📈 Monthly Revenue Trend")
    monthly_revenue = df_filtered.groupby('Month')['Revenue'].sum().reset_index()
    fig_line = px.line(monthly_revenue, x='Month', y='Revenue',
                      labels={'Revenue': 'Revenue (£)', 'Month': 'Month'},
                      markers=True)
    fig_line.update_traces(line_color='#2563eb', line_width=3, marker_size=10)
    fig_line.update_layout(height=400, hovermode='x unified')
    st.plotly_chart(fig_line, use_container_width=True)

with col_right:
    st.subheader("📦 Top 10 Products")
    top_products = df_filtered.groupby('Description')['Revenue'].sum().nlargest(10).reset_index()
    fig_bar = px.bar(top_products.sort_values('Revenue'), 
                    x='Revenue', y='Description', orientation='h',
                    labels={'Revenue': 'Revenue (£)', 'Description': 'Product'},
                    color='Revenue', color_continuous_scale='Blues')
    fig_bar.update_layout(height=400, showlegend=False)
    st.plotly_chart(fig_bar, use_container_width=True)

st.markdown("---")

# Full-width chart
st.subheader("🔥 Revenue Heatmap by Month and Day of Week")
df_filtered['DayOfWeek'] = df_filtered['InvoiceDate'].dt.day_name()
heatmap_data = df_filtered.groupby(['Month', 'DayOfWeek'])['Revenue'].sum().reset_index()
heatmap_pivot = heatmap_data.pivot(index='DayOfWeek', columns='Month', values='Revenue')

# Reorder days
day_order = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday']
heatmap_pivot = heatmap_pivot.reindex(day_order)

fig_heatmap = px.imshow(heatmap_pivot,
                        labels=dict(x="Month", y="Day of Week", color="Revenue (£)"),
                        color_continuous_scale='RdYlGn',
                        aspect="auto")
fig_heatmap.update_layout(height=400)
st.plotly_chart(fig_heatmap, use_container_width=True)

st.markdown("---")

# Data Table
with st.expander("📋 View Raw Data"):
    st.dataframe(df_filtered[['InvoiceNo', 'Description', 'Quantity', 
                              'UnitPrice', 'Revenue', 'InvoiceDate', 'CustomerID']].head(100),
                use_container_width=True)

# Footer
st.markdown("---")
st.markdown("""
    <div style='text-align: center; color: #64748b;'>
        <p>Built with ❤️ using Streamlit | Data: UCI Machine Learning Repository</p>
    </div>
""", unsafe_allow_html=True)
'''

# Write to file
with open('streamlit_app.py', 'w', encoding='utf-8') as f:
    f.write(streamlit_code)

print("✅ Created streamlit_app.py successfully!")
print("\n📝 To run the app, open a terminal and run:")
print("   streamlit run streamlit_app.py")
print("\n💡 The app will open in your browser at http://localhost:8501")

### 🚀 Step 2: Run Your Streamlit App

After running the cell above to create `streamlit_app.py`:

**Option 1: Run from Terminal**
```bash
streamlit run streamlit_app.py
```

**Option 2: Run from VS Code Terminal**
1. Open Terminal in VS Code (`` Ctrl+` ``)
2. Type: `streamlit run streamlit_app.py`
3. Press Enter

The app will open in your browser at `http://localhost:8501`

---

### 🎛️ Streamlit Widget Examples

Here are common widgets you can use:

In [ ]:
# Streamlit Widget Reference Guide
# (These examples show the syntax - copy them to your streamlit_app.py)

print("🎛️ STREAMLIT WIDGETS CHEAT SHEET")
print("="*70)

widget_examples = """
# === INPUT WIDGETS ===

# 1. Text Input
name = st.text_input("Enter your name", "John Doe")

# 2. Number Input
age = st.number_input("Enter age", min_value=0, max_value=120, value=25)

# 3. Slider
threshold = st.slider("Select threshold", 0, 100, 50)

# 4. Select Box (Dropdown)
option = st.selectbox("Choose option", ["Option A", "Option B", "Option C"])

# 5. Multi-select
options = st.multiselect("Choose multiple", ["A", "B", "C", "D"])

# 6. Checkbox
agree = st.checkbox("I agree")

# 7. Radio Buttons
choice = st.radio("Choose one", ["Yes", "No", "Maybe"])

# 8. Date Input
date = st.date_input("Select date")

# 9. Time Input
time = st.time_input("Select time")

# 10. File Uploader
file = st.file_uploader("Upload CSV", type=['csv'])

# === DISPLAY WIDGETS ===

# 1. Metric Cards
st.metric("Revenue", "$1.2M", "+12%")

# 2. Progress Bar
st.progress(75)

# 3. Status Messages
st.success("Success!")
st.error("Error!")
st.warning("Warning!")
st.info("Info!")

# 4. Expander (Collapsible)
with st.expander("Click to expand"):
    st.write("Hidden content")

# 5. Columns (Side-by-side)
col1, col2 = st.columns(2)
with col1:
    st.write("Left column")
with col2:
    st.write("Right column")

# 6. Tabs
tab1, tab2 = st.tabs(["Tab 1", "Tab 2"])
with tab1:
    st.write("Content 1")
with tab2:
    st.write("Content 2")

# === BUTTONS & ACTIONS ===

# Button
if st.button("Click me"):
    st.write("Button clicked!")

# Download Button
st.download_button("Download CSV", data=df.to_csv(), file_name="data.csv")

# Form (Group inputs)
with st.form("my_form"):
    name = st.text_input("Name")
    age = st.number_input("Age")
    submitted = st.form_submit_button("Submit")
    if submitted:
        st.write(f"Hello {name}, age {age}")
"""

print(widget_examples)

print("\n💡 Copy these examples into your streamlit_app.py to test them!")
print("📚 Full docs: https://docs.streamlit.io/library/api-reference")

---

# Part 3: Deployment Guide

## 3.1 Deploying to Streamlit Cloud (FREE!)

### Prerequisites:
- ✅ GitHub account
- ✅ Your Streamlit app file (`streamlit_app.py`)
- ✅ `requirements.txt` file

### Step-by-Step Deployment:

**1. Prepare Your Files**
```
your-project/
├── streamlit_app.py      # Your main app
├── requirements.txt       # Dependencies
└── README.md             # Optional documentation
```

**2. Create GitHub Repository**
- Go to https://github.com and create a new repository
- Push your code to GitHub

**3. Deploy to Streamlit Cloud**
- Go to https://share.streamlit.io
- Sign in with GitHub
- Click "New app"
- Select your repository and file
- Click "Deploy"

**4. Your App is Live!** 🎉
- You'll get a URL like: `https://your-app.streamlit.app`
- Share it with anyone!

---

## 3.2 Deploying to Other Platforms

### Option 1: Heroku
```bash
# Create Procfile
web: streamlit run streamlit_app.py --server.port $PORT

# Deploy
heroku create your-app-name
git push heroku main
```

### Option 2: AWS/GCP/Azure
- Use Docker container
- Deploy to cloud compute service
- Configure ports and environment

### Option 3: Local Network (Company)
```bash
# Run on specific port and host
streamlit run streamlit_app.py --server.port 8501 --server.address 0.0.0.0
```

Then access from other computers: `http://YOUR-IP:8501`

---

## 3.3 Best Practices for Production

### ✅ Performance Optimization

1. **Use Caching**
```python
@st.cache_data  # For data loading
def load_data():
    return pd.read_csv('data.csv')

@st.cache_resource  # For ML models
def load_model():
    return joblib.load('model.pkl')
```

2. **Lazy Loading**
- Only load data when needed
- Use st.session_state to store data between reruns

3. **Optimize Data Size**
- Filter data before displaying
- Use sampling for large datasets
- Compress data files

### 🔒 Security Considerations

1. **Hide Secrets**
```python
# Use st.secrets instead of hardcoding
api_key = st.secrets["api_key"]
```

2. **Validate User Input**
```python
if st.text_input("Enter value"):
    # Validate input before processing
    pass
```

3. **Rate Limiting**
- Implement API rate limits
- Use authentication if needed

### 📊 Monitoring

- Add Google Analytics
- Track user interactions
- Monitor errors with Sentry
- Set up uptime monitoring

---

# Part 4: Final Project - Complete Dashboard

## 🎯 Project Requirements

Build a **complete e-commerce analytics dashboard** with the following features:

### Required Features:

1. **📊 KPI Metrics (Top of page)**
   - Total Revenue
   - Number of Orders
   - Unique Customers
   - Average Order Value
   - Growth % indicators

2. **🎛️ Interactive Filters (Sidebar)**
   - Date range picker
   - Product category selector
   - Country selector
   - Customer segment filter

3. **📈 Visualizations (Minimum 5)**
   - Monthly revenue trend (line chart)
   - Top products by revenue (bar chart)
   - Customer segmentation (pie chart)
   - Revenue heatmap by day/hour
   - Cohort retention analysis

4. **📋 Data Tables**
   - Expandable raw data viewer
   - Top customers table
   - Product performance table

5. **🎨 Design Requirements**
   - Professional color scheme
   - Responsive layout (columns)
   - Clear titles and labels
   - Helpful descriptions
   - Mobile-friendly

6. **⚡ Performance**
   - Use `@st.cache_data` for data loading
   - Optimize query performance
   - Handle large datasets gracefully

---

## 📝 Grading Rubric (100 points)

| Criteria | Points | Description |
|----------|--------|-------------|
| **Functionality** | 40 | All required features working correctly |
| **Visualizations** | 25 | 5+ interactive charts, well-designed |
| **Interactivity** | 15 | Filters update all charts correctly |
| **Code Quality** | 10 | Clean, commented, organized code |
| **Design/UX** | 10 | Professional appearance, easy to use |

---

## 💡 Bonus Features (+10 points each)

- 🔐 User authentication
- 📊 Advanced analytics (RFM, cohort, forecasting)
- 📁 File upload functionality
- 📥 Data export (CSV/Excel download)
- 🎬 Animated visualizations
- 🗺️ Geographic maps
- 📱 Multi-page app with navigation

---

## 🚀 Getting Started

1. **Start with the template** from earlier in this notebook
2. **Add filters** to sidebar
3. **Connect filters to charts** (filter dataframe)
4. **Add more visualizations** one by one
5. **Style your app** with custom CSS
6. **Test thoroughly** with different filter combinations
7. **Deploy to Streamlit Cloud**
8. **Submit your GitHub repo link**

---

## 📚 Resources

- **Streamlit Docs**: https://docs.streamlit.io
- **Plotly Docs**: https://plotly.com/python/
- **Streamlit Gallery**: https://streamlit.io/gallery (for inspiration)
- **Color Palettes**: https://coolors.co
- **Icons**: Use emoji or Font Awesome

---

## ✅ Submission Checklist

Before submitting, make sure you have:

- [ ] All 5 required visualizations working
- [ ] Filters update all charts
- [ ] Code is commented and organized
- [ ] `requirements.txt` is complete
- [ ] README.md with app description
- [ ] App deployed to Streamlit Cloud
- [ ] GitHub repository is public
- [ ] Screenshots of your app in README

---

Good luck with your project! 🚀

---

# 📖 Summary & Key Takeaways

## What We Learned

### 1. **Plotly Interactive Charts**
- ✅ Hover tooltips, zoom, pan functionality
- ✅ Plotly Express for quick charts
- ✅ Graph Objects for custom layouts
- ✅ Subplots for dashboards
- ✅ Animations for time-series

### 2. **Streamlit Web Apps**
- ✅ Pure Python, no HTML/CSS needed
- ✅ Built-in widgets (sliders, filters, buttons)
- ✅ `@st.cache_data` for performance
- ✅ Columns and layouts
- ✅ Real-time interactivity

### 3. **Deployment**
- ✅ Streamlit Cloud (free, easy)
- ✅ Heroku, AWS, GCP options
- ✅ GitHub integration
- ✅ Public URL sharing

---

## 🎯 When to Use What?

| Tool | Best For | Pros | Cons |
|------|----------|------|------|
| **Matplotlib** | Reports, papers | Publication quality, full control | Static, no interaction |
| **Seaborn** | Statistical plots | Beautiful defaults, quick | Static, limited customization |
| **Plotly** | Web dashboards | Interactive, modern | Larger files, learning curve |
| **Streamlit** | Data apps, demos | Fast development, Python-only | Less control than full web frameworks |
| **Dash** | Production apps | More control, scalable | More complex, steeper learning |

---

## 💡 Best Practices Summary

### Design
- 🎨 Use consistent color schemes
- 📊 Label everything clearly
- 🔍 Make filters obvious
- 📱 Test on mobile devices

### Performance
- ⚡ Cache expensive operations
- 📉 Downsample large datasets
- 🗜️ Compress data files
- 🔄 Lazy load when possible

### Code
- 📝 Comment your code
- 🧩 Break into functions
- 🔒 Hide secrets properly
- ✅ Test edge cases

### Deployment
- 📦 Include requirements.txt
- 📄 Write clear README
- 🚀 Test before deploying
- 📊 Monitor usage

---

## 🎓 Next Steps

1. **Complete the final project**
2. **Explore Streamlit gallery** for inspiration
3. **Learn Dash** for more control
4. **Add ML models** to your dashboards
5. **Build a portfolio project**

---

## 📚 Additional Resources

### Documentation
- 📖 [Plotly Python](https://plotly.com/python/)
- 📖 [Streamlit Docs](https://docs.streamlit.io)
- 📖 [Dash Documentation](https://dash.plotly.com)

### Tutorials
- 🎥 [Streamlit YouTube Channel](https://www.youtube.com/@streamlitofficial)
- 🎓 [DataCamp Plotly Course](https://www.datacamp.com/courses/interactive-data-visualization-with-plotly-in-python)
- 📝 [Real Python Streamlit Tutorial](https://realpython.com/streamlit-python-dashboards/)

### Inspiration
- 🎨 [Streamlit Gallery](https://streamlit.io/gallery)
- 💡 [Plotly Chart Studio](https://chart-studio.plotly.com/feed/)
- 🏆 [Awesome Streamlit](https://github.com/MarcSkovMadsen/awesome-streamlit)

---

## 🙏 Thank You!

Selamat! Anda telah menyelesaikan **Module 4: Interactive Dashboards**!

**Apa yang Anda sudah bisa:**
- ✅ Create interactive visualizations with Plotly
- ✅ Build web applications with Streamlit
- ✅ Deploy dashboards to the cloud
- ✅ Design user-friendly interfaces
- ✅ Optimize for performance

**Now go build something amazing!** 🚀

---

### 📧 Questions or Feedback?

Jika ada pertanyaan tentang module ini, silakan:
1. Check the documentation links above
2. Ask in the course forum
3. Email your instructor
4. Post on Stack Overflow with #streamlit or #plotly tags

**Happy dashboard building!** 📊✨